In [1]:
# Импортирование библиотек для иницализации основных параметров системы
from fortran_calc_tools import *

# Импортирование неодходимых библиотек
from os import path 
import time
import pandas as pd, numpy as np
from collections import namedtuple
from calc_tools import pairwise_1, pairwise_2
from scipy.linalg import logm, expm, sqrtm, eig, lu, lu_factor, lu_solve
from multiprocessing import Pool
from numpy.linalg import inv
from numpy import linalg as LA

# Импортирование библиотек для визуализации данных !!!!!
import matplotlib.pyplot as plot
import matplotlib as mpl
import seaborn as sns
import plotly as pt
import plotly.express as px
%matplotlib inline
import plotly.graph_objects as go

In [2]:
# Задание значении характеристик материала для фаз и троса
#                         GM    OPM    S     XA   YA
Faza_A = Fazy("Фаза А", 35.336, 1.0, 150.0, 0.0, 19.0)
Faza_B = Fazy("Фаза В", 35.336, 1.0, 150.0, 6.3, 19.0)
Faza_C = Fazy("Фаза С", 35.336, 1.0, 150.0, 4.2, 25.0)
Tross = Fazy("Тросс", 17.336, 4000.0, 50.0, 2.1, 28.0)

# В данном случае у нас будет 50 гармоник от [1 до 50]
garmoniki = Garmoniki(50)

# Создание объекта для проведения расчетов
rashet = Rachety()

# Инициализация объекта для подстанции "Зеленая" и чтение файла
basepath = path.abspath('')
filepath = path.abspath(path.join(basepath, "..", path.join("data", "Данные ПС Сарепта1.xls")))
PodS_zelenaya = PodStans(filepath, volt=110, harm_num=49)

dummy_str_input = "fuzzBuzz for testing"
dummy_int_input = 404

system = System(PodS_zelenaya, garmoniki, rashet, Fazy, dummy_str_input, dummy_str_input, dummy_int_input, dummy_int_input,
     dummy_int_input, dummy_int_input, dummy_int_input)

# Установка конфигурации для выведения данных
pd.set_option('display.max_columns', 50)
pd.set_option('display.max_rows', 50)

In [3]:
#                   !!! DEBUGGING PROCESS HERE !!!

In [128]:
# GETTING MAIN LINE CHARACTERISTICS FROM EXCEL FILE
UM, FUM, AIM, FIM, funu, fu, funi, fi, knsu, knsi, rmsu, rmsi = system.line_matrix(1)

In [129]:
# DECLARING VARIABLES

WD = np.zeros((2, 50))
PD = np.zeros((3, 700))

UM1 = np.zeros((700, UM.shape[1],UM.shape[2]))
UM2 = np.zeros((700, UM.shape[1],UM.shape[2]))
AIM1 = np.zeros((700, UM.shape[1],UM.shape[2]))
AIM2 = np.zeros((700, UM.shape[1],UM.shape[2]))
PPR1 = np.zeros((700))

PPP = np.zeros((1000, 50)); PPP1 = np.zeros((1000, 50));
PPP2 = np.zeros((1000, 50)); PPP3 = np.zeros((1000, 50));
PPP4 = np.zeros((1000, 50)); PPP5 = np.zeros((1000, 50));
PPP6 = np.zeros((1000, 50)); PPP7 = np.zeros((1000, 50));
PPP8 = np.zeros((1000, 50));

# !!!!!!!!!!!!!!!!! CordN = 8 was in original here 
cordN = 4
UK1 = np.array([complex(0, 0) for _ in range(cordN)], dtype="complex128")
AIK1 = np.array([complex(0, 0) for _ in range(cordN)], dtype="complex128")

UK10 = complex(0, 0); UK11 = complex(0, 0); UK12 = complex(0, 0);
AIK10 = complex(0, 0); AIK11 = complex(0, 0); AIK12 = complex(0, 0);
AL = complex(0, 0);

PP1 = 0.0
PP2 = 0.0
RZ = 35.3

In [130]:
# Implementing RASCHET fortran's subroutine in python
def RASCHET(NN, LL):
# LL is in range [0-559] NN [0-49]

#     if NN == 1:
#         raise ValueError
        
#     if LL > 49:
#         LL = 49
    
    global UK1,AIK1,PPP,PP1,PP2,PPP1,PPP2,PPP3,PPP4,PPP5,PPP6,PPP7,PPP8, MM,M,M1,MT,M10,M20,PR,K1,K2,K3,N1,N2,N3,MPR,MTR,MMT
    
    
    XA, YA, OMP, GM, S = Fazy.construc_matrices()
    R0, R, UXM, HI, R11, DET2, DET4 = np.zeros((M)), np.zeros((M)), np.zeros((M)), np.zeros((M)), np.zeros((M)), np.zeros((M)), np.zeros((M))
    EVU, B, UX, AIX, UK1, AIK1, SM, EVI, DET1, DET3, BB, AIXM, AA = np.zeros((M)), np.zeros((M), dtype="complex128"), np.zeros((M), dtype="complex128"), np.zeros((M), dtype="complex128"), np.zeros((M), dtype="complex128"), np.zeros((M), dtype="complex128"), np.zeros((M), dtype="complex128"), np.zeros((M)), np.zeros((M), dtype="complex128"), np.zeros((M), dtype="complex128"), np.zeros((M)), np.zeros((M)), np.zeros((M)),
    B1, B4, B5 = np.zeros((M20), dtype="complex128"), np.zeros((M20)), np.zeros((M20), dtype="complex128")
    B6, B10, B7 = np.zeros((M10)), np.zeros((M10), dtype="complex128"), np.zeros((M10)) 
    
    DET10, DET20, SS, SS1, EX1,  = [], [], [], [], []
    
    HC1, HC2, HC3, HC4, F10, XL, XL1, G, D, HC, UXM = np.zeros((M, M)), np.zeros((M, M)), np.zeros((M, M)), np.zeros((M, M)), np.zeros((M, M)), np.zeros((M, M)), np.zeros((M, M)), np.zeros((M, M)), np.zeros((M, M)), np.zeros((M, M)), np.zeros((M, M)) 
    Z, Y, AU, E,  AAI, F, F1 = np.zeros((M, M), dtype="complex128"), np.zeros((M, M), dtype="complex128"), np.zeros((M, M)), np.zeros((M, M), dtype="complex128"), np.zeros((M, M)), np.zeros((M, M), dtype="complex128"), np.zeros((M, M), dtype="complex128")
    F2, D1, D2, D3, LU, LI = np.zeros((M, M)), np.zeros((M, M)), np.zeros((M, M)), np.zeros((M, M)), np.zeros((M, M), dtype="complex128"), np.zeros((M, M), dtype="complex128")
    LU1, LI1, LU2, LU3, LI2, LI3 = np.zeros((M, M), dtype="complex128"), np.zeros((M, M), dtype="complex128"), np.zeros((M, M), dtype="complex128"), np.zeros((M, M), dtype="complex128"), np.zeros((M, M), dtype="complex128"), np.zeros((M, M), dtype="complex128")
    F3, F4, F5, F6, F7 = np.zeros((M, M)), np.zeros((M, M)), np.zeros((M, M)), np.zeros((M, M)), np.zeros((M, M))
    HH13, HH14, HH21, HH22, HH23 = np.zeros((M, M), dtype="complex128"), np.zeros((M, M), dtype="complex128"), np.zeros((M, M), dtype="complex128"), np.zeros((M, M), dtype="complex128"), np.zeros((M, M), dtype="complex128")
    HH31, HH32, HH33, HH34, HH24 = np.zeros((M, M), dtype="complex128"), np.zeros((M, M), dtype="complex128"), np.zeros((M, M), dtype="complex128"), np.zeros((M, M), dtype="complex128"), np.zeros((M, M), dtype="complex128")
    HH41, HH42, HH43, HH44, HH = np.zeros((M, M), dtype="complex128"), np.zeros((M, M), dtype="complex128"), np.zeros((M, M), dtype="complex128"), np.zeros((M, M), dtype="complex128"), np.zeros((M10, M10))
    CC, DD, HH11, HH12 = np.zeros((M, M)), np.zeros((M, M)), np.zeros((M, M), dtype="complex128"), np.zeros((M, M), dtype="complex128")
    A1, A2 = np.zeros((M1, M1), dtype="complex128"), np.zeros((M1, M1), dtype="complex128")
    
    AG, GG = np.zeros((M1, M, M), dtype=type), np.zeros((M20, M20), dtype="complex128")
    GG1, GG2, GG3, GG4, GG5 = np.zeros((M20, M20), dtype="complex128"), np.zeros((M20, M20), dtype="complex128"), np.zeros((M10, M20), dtype="complex128"), np.zeros((M10, M10), dtype="complex128"), np.zeros((M10, M10), dtype="complex128")
    IPVT1, IH = np.zeros((M1)), np.array([1, 1, 1, 1, 1, 1, 1, 0, 0, 0, 0, 1, 0, 0, 0, 0])
    
    if PR == 1:
        PP1 = 0
    if PR == 2:
        PP2 = 0
#     PPP[NN, LL] = 0
#     PPP1[NN, LL] = 0
#     PPP2[NN, LL] = 0
#     PPP3[NN, LL] = 0
#     PPP4[NN, LL] = 0
#     PPP5[NN, LL] = 0
#     PPP6[NN, LL] = 0
#     PPP7[NN, LL] = 0
#     PPP8[NN, LL] = 0
    
    MMT = MM / MT
    W = float(LL+1)
    print(W)
    EX1 = complex(2.71828, 0)
    
    # WRITING INTO UNIT 5. LINE MAIN CHARACTERISTIC
    
    for i in range(M):
        R[i]=np.sqrt(S[i]/np.pi)/1000.
        HI[i]=R[i]/(2.)*np.sqrt(2*np.pi*W*50*4*np.pi*OMP[i]*GM[i]/20)
        R0[i]=1000/(GM[i]*S[i])
        if HI[i] < 1:
            R11[i]=R0[i]*(1+HI[i]**4/3)
        if HI[i] > 1: 
            R11[i]=R0[i]*(HI[i]+0.25+3./(64.*HI[i]))
        if i+1 == M:
            pass
            # WRITE R11's values INTO THE FILE "R11"

    # 845 - 12
    for i in range(M10):
        for j in range(M10):
            HH[i,j] = 0 

    # 12 - 161
    for i in range(M):
        for j in range(M):
            if i == j:
                D[i,i] = R[i]
            if i != j:
                D[i,j]=np.sqrt((XA[i]-XA[j])**2+(YA[i]-YA[j])**2)
            HC[i,j]=np.sqrt((XA[i]-XA[j])**2+(YA[i]+YA[j])**2)
            E[i,j]=complex(0.0, 0.0)
            E[i,i]=complex(1.0, 0.0)

    # 161 - 740
    for i in range(M):
        for j in range(M):
            XL1[i,j]=(0.145*np.log10(1000/D[i,j]))/(100*np.pi)
    
    # 740 - 743
    for i in range(M):
        for j in range(M):
            HC1[i,j]=41.4*10**6*np.log10(HC[i,j]/D[i,j])
    
    # 743 - 744
    HC1 = HC1.astype('float64')
    HC3 = DLINRG(HC1)
    F10 = DMRRRR(HC1,HC3)
    
    for i in range(M):
        for j in range(M):
            HC2[i,j]=HC3[i,j]*2.*np.pi*50
    
    # 744 - 847
    for i in range(M):
        for j in range(M):
            XL[i,j]=XL1[i,j]*W*2*50*np.pi
            HC4[i,j]=HC2[i,j]*W
            R10=0.0
            if i == j:
                Z[i,j]=complex(R11[i],XL[i,j]) 
            if i != j:
                Z[i,j]=complex(R10,XL[i,j])
            if i == j:
                G[i,j]=0.00000004*YA[i]/YA[i] 
            if i != j:
                G[i,j]=-0.00000004*YA[0]/D[i,j] 
            G[i,j]=0.
            Y[i,j]=complex(G[i,j],HC4[i,j])
    print("CHECK :", XL) # <<< ------- THE REAL PROBLEM IS HERE !!!!!!!!!!!!!!!!!
#     print("G:", G)
#     print("Y:", Y)
#     print("Z:", Z)
    
    # 847 - the end of subroutine        
    for III in range(MT): # <----- main loop # 1300
#         print("Main loop counter MT: ", III)
        
        if M != 3: # GOTO 767
#             print("Here 3")
            if (M != 4): # GOTO 768
#                 print("Here 4")
                if (M != 6): # GOTO 769
#                     print("Here 6")
                    if (M != 7): # GOTO 770
#                         print("Here 7")
                        if (M != 8): # GOTO 771
                            pass
#                             print("Here 8")

                        else:
                            print("else 8")
                            # 770 - 766
                            for i in range(3):
                                B5[i]=UK1[i]
                                B5[i+3]=UK1[i]
                                B5[MPR+1-1]=complex(0.,0.)
                                B5[MPR+2-1]=complex(0.,0.)
                                B5[i+M]=AIK1[i]
                                B5[i+M+3]=AIK1[i]
                                B5[2*M-1-1]=complex(0.,0.)
                                B5[2*M-1]=complex(0.,0.)
                                B5[i+2*M]=complex(0.,0.)
                                B5[i+2*M+3]=complex(0.,0.)
                                B5[3*M-1-1]=complex(0.,0.)
                                B5[3*M-1]=complex(0.,0.)
                                B5[i+3*M]=complex(0.,0.)
                                B5[i+3*M+3]=complex(0.,0.)
                                B5[4*M-1-1]=complex(0.,0.)
                                B5[4*M-1]=complex(0.,0.)
                          
                    else:
                        print("else 7")
                        # 769 - 765
                        for i in range(3):
                            B5[i]=UK1[i]
                            B5[i+3]=UK1[i] 
                            B5[M-1]=complex(0.,0.) 
                            B5[i+M]=AIK1[i]
                            B5[i+M+3]=AIK1[i] 
                            B5[2*M-1]=complex(0.,0.)
                            B5[i+2*M]=complex(0.,0.)
                            B5[i+2*M+3]=complex(0.,0.)
                            B5[3*M-1]=complex(0.,0.)
                            B5[i+3*M]=complex(0.,0.)
                            B5[i+3*M+3]=complex(0.,0.)
                            B5[4*M-1]=complex(0.,0.)
                      

                else:
                    print("else 6")
                    # 768 - 764
                    for i in range(3):
                        B5[i]=UK1[i]
                        B5[i+3]=UK1[i]
                        B5[i+M]=AIK1[i]
                        B5[i+M+3]=AIK1[i]
                        B5[i+2*M]=complex(0.,0.)
                        B5[i+2*M+3]=complex(0.,0.)
                        B5[i+3*M]=complex(0.,0.)
                        B5[i+3*M+3]=complex(0.,0.)

            else:
#                 print("else 4")
                # 767 - 762
                for i in range(3):
    #   !!!!!!!!!!!!!!!!!!!!   AIK1 and UK1 ARE THE REAL EVILS IN THIS PARTY !!!!!!!!!!!!!!!!!!!!!!!!
#                     print("AIK1[i]: ", AIK1[i])
#                     print("UK1[i]: ",UK1[i])
                    B5[i]=UK1[i]
                    B5[M-1]=complex(0.,0.)
                    B5[i+M]=AIK1[i]
                    B5[2*M-1]=complex(0.,0.)
                    B5[i+2*M]=complex(0.,0.)
                    B5[3*M-1]=complex(0.,0.)
                    B5[i+3*M]=complex(0.,0.)
                    B5[4*M-1]=complex(0.,0.)
                
        else:
            print("else 3")
            # 847 - 761
            for i in range(3):
                B5[i]=UK1[i]
                B5[i+3]=AIK1[i]
                B5[i+6]=complex(0.,0.)
                B5[i+9]=complex(0.,0.)
            
        # <->-- ???? DEBUGGING
        
       #   !!!!!!!!!!!!!!!!!!!!   B5 IS THE REAL EVIL IN THIS PARTY !!!!!!!!!!!!!!!!!!!!!!!!
#         print("B5: ", B5)
        
        AU = DMCRCR(Z,Y)
        SS1=np.sqrt(AU[0,0])
        EVU = DEVLCG(AU)
        
        # IMPORTANT POINT
        for j in range(M):
            for i in range(M):
                F[i,j]=EVU[i]**j # (j-1) was in the first case
                F1[i,j]=F[i,j]
        
        for i in range(M1):
            for j in range(M1):
                A1[i,j]=F[i,j]

        A2 = DLFTCG(A1)
        SS = DET10 = DLFDCG(A2); DET20 = 1 # parameters DET10,DET20 were in function call
        # SS=DET10*(10.**DET20)
        
        for j in range(M1):

            for ii in range(M1):
                for jj in range(M1):
                    F[ii,jj]=F1[ii,jj]

            for i in range(M1):
                F[i,j]=EVU[i]**0.5

            for ii in range(M1):
                for jj in range(M1):
                    A1[ii,jj]=F[ii,jj]

            A2 = DLFTCG(A1)
            DET1[j] = DLFDCG(A2); DET2[j] = 1 # parameters DET1(J), DET2(J) were in function call

        F2 = DMCRCR(AU,AU)
        F3 = DMCRCR(F2,AU)
        F4 = DMCRCR(F3,AU)
        F5 = DMCRCR(F4,AU)
        F6 = DMCRCR(F5,AU)
        F7 = DMCRCR(F6,AU)
        
        for i in range(M1):
            for ii in range(M):
                for jj in range(M):

                    if i == 0:
                        AG[0,ii,jj]=E[ii,jj]
                    if i == 1:
                        AG[1,ii,jj]=AU[ii,jj]
                    if i == 2:
                        AG[2,ii,jj]=F2[ii,jj]
                    if i == 3:
                        AG[3,ii,jj]=F3[ii,jj]
                    if i == 4:
                        AG[4,ii,jj]=F4[ii,jj]
                    if i == 5:
                        AG[5,ii,jj]=F5[ii,jj]
                    if i == 6:
                        AG[6,ii,jj]=F6[ii,jj]
                    if i == 7:
                        AG[7,ii,jj]=F7[ii,jj]

        for ii in range(M):
            for jj in range(M):
                LU[ii,jj]=0.

        for i in range(M1):
            DET3[i]=DET1[i]/DET10
            DET4[i]=DET2[i]-DET20
            for ii in range(M):
                for jj in range(M):
                    LU[ii,jj]=LU[ii,jj]+AG[i,ii,jj]*DET3[i]*(10**DET4[i])
        
        F3 = DMCRCR(LU,LU)
        AAI = DMCRCR(Y,Z)
        EVI = DEVLCG(AAI)
  
        for j in range(M):
            for i in range(M):
                F[i,j] = EVI[i]**j # j-1
                F1[i,j] = F[i,j]

        for i in range(M1):
            for j in range(M1):
                A1[i,j]=F[i,j]

        A2 = DLFTCG(A1)
        DET10 = DLFDCG(A2); DET20 = 1 # parameters DET10,DET20 were in function call
        
        for j in range(M1):
            for ii in range(M1):
                for jj in range(M1):
                    F[ii,jj]=F1[ii,jj]

            for i in range(M1):
                F[i,j]=EVI[i]**0.5
            for ii in range(M1):
                for jj in range(M1):
                    A1[ii,jj]=F[ii,jj]

            A2 = DLFTCG(A1)
            DET1[j] = DLFDCG(A2); DET2[j] = 1 # parameters DET1(J),DET2(J) were in function call
            
        F2 = DMCRCR(AAI,AAI)
        F3 = DMCRCR(F2,AAI,)
        F4 = DMCRCR(F3,AAI)
        F5 = DMCRCR(F4,AAI)
        F6 = DMCRCR(F5,AAI)
        F7 = DMCRCR(F6,AAI)

        for i in range(M1):
            for ii in range(M):
                for jj in range(M):

                    if i == 0:
                        AG[0,ii,jj]=E[ii,jj]
                    if i == 1:
                        AG[1,ii,jj]=AAI[ii,jj]
                    if i == 2:
                        AG[2,ii,jj]=F2[ii,jj]
                    if i == 3:
                        AG[3,ii,jj]=F3[ii,jj]
                    if i == 4:
                        AG[4,ii,jj]=F4[ii,jj]
                    if i == 5:
                        AG[5,ii,jj]=F5[ii,jj]
                    if i == 6:
                        AG[6,ii,jj]=F6[ii,jj]
                    if i == 7:
                        AG[7,ii,jj]=F7[ii,jj]

        for ii in range(M):
            for jj in range(M):
                LI[ii,jj]=0.

        for i in range(M1):
            for ii in range(M):
                for jj in range(M):
                    LI[ii,jj]=LI[ii,jj]+(DET1[i]*(10**DET2[i])*AG[i,ii,jj])/(DET10*(10**DET20))
        
        F3 = DMCRCR(LI,LI)
        LM=MMT
        
        for n, _ in enumerate(range(2), start=1):

            if n == 1:
                SA=-1.
            if n == 2:
                SA=1.

            for ii in range(M):
                for jj in range(M):
                    LU1[ii,jj]=SA*MMT*LU[ii,jj]


            EVU = DEVLCG(LU1)
            for i in range(M):
                for j in range(M):
                    F[i,j]=EVU[i]**j # (j-1) here was an expression (j-1)


            for ii in range(M):
                for jj in range(M):
                    F1[ii,jj]=F[ii,jj]


            for ii in range(M1):
                for jj in range(M1):
                    A1[ii,jj]=F[ii,jj]
            
            A2 = DLFTCG(A1)
            DET10 = DLFDCG(A2); DET20 = 1 # DET10 and DET20 were the arguments of this function
            
            for j in range(M):
                for ii in range(M):
                    for jj in range(M):
                        F[ii,jj]=F1[ii,jj]


                for i in range(M):
#                     F = F.astype("complex128")
                    F[i,j]=EX1**EVU[i]


                for ii in range(M1):
                    for jj in range(M1):
                        A1[ii,jj]=F[ii,jj]


                A2 = DLFTCG(A1)
#                 A2 = A2.astype('float64')
                DET1[j] = DLFDCG(A2); DET2[j] = 1
            
            F2 = DMCRCR(LU1,LU1)
            F3 = DMCRCR(F2,LU1)
            F4 = DMCRCR(F3,LU1)
            F5 = DMCRCR(F4,LU1)
            F6 = DMCRCR(F5,LU1)
            F7 = DMCRCR(F6,LU1)

            for i in range(M1):
                for ii in range(M):
                    for jj in range(M):

                        if i == 0:
                            AG[0,ii,jj]=E[ii,jj]
                        if i == 1:
                            AG[1,ii,jj]=LU1[ii,jj]
                        if i == 2:
                            AG[2,ii,jj]=F2[ii,jj]
                        if i == 3:
                            AG[3,ii,jj]=F3[ii,jj]
                        if i == 4:
                            AG[4,ii,jj]=F4[ii,jj]
                        if i == 5:
                            AG[5,ii,jj]=F5[ii,jj]
                        if i == 6:
                            AG[6,ii,jj]=F6[ii,jj]
                        if i == 7:
                            AG[7,ii,jj]=F7[ii,jj]

            for ii in range(M):
                for jj in range(M):
                    LU2[ii,jj]=0.

            for i in range(M1):
                for ii in range(M):
                    for jj in range(M):
                        LU2[ii,jj]=LU2[ii,jj]+(DET1[i]*(10**DET2[i])*AG[i,ii,jj])/(DET10*(10**DET20))

            if n == 2:
                F2 = DMCRCR(LU3,LU2)
                continue
            else:
                for ii in range(M):
                    for jj in range(M):
                        LU3[ii,jj]=LU2[ii,jj]

        for n in range(2):
            if n == 0:
                SA=-1
            if n == 1:
                SA=1

            for ii in range(M):
                for jj in range(M):
                    LI1[ii,jj]=SA*MMT*LI[ii,jj]

            EVI = DEVLCG(LI1)

            for i in range(M):
                for j in range(M):
                    F[i,j]=EVI[i]**j # J-1 in original

            for ii in range(M):
                for jj in range(M):
                    F1[ii,jj]=F[ii,jj]

            for ii in range(M1):
                for jj in range(M1):
                    A1[ii,jj]=F[ii,jj]

            A2 = DLFTCG(A1)
            DET10 = DLFDCG(A2); DET20 = 1
            
            for j in range(M):
                for ii in range(M):
                    for jj in range(M):
                        F[ii,jj]=F1[ii,jj]

                for i in range(M):
                    F[i,j]=EX1**EVI[i]

                for ii in range(M1):
                    for jj in range(M1):
                        A1[ii,jj]=F[ii,jj]

                A2 = DLFTCG(A1)
                DET1[j] = DLFDCG(A2); DET2[j] = 1


            F2 = DMCRCR(LI1,LI1)
            F3 = DMCRCR(F2,LI1)
            F4 = DMCRCR(F3,LI1)
            F5 = DMCRCR(F4,LI1)
            F6 = DMCRCR(F5,LI1)
            F7 = DMCRCR(F6,LI1)
            
            for i in range(M1):
                for ii in range(M):
                    for jj in range(M):
                        if i == 0:
                            AG[0,ii,jj]=E[ii,jj]
                        if i == 1:
                            AG[1,ii,jj]=LI1[ii,jj]
                        if i == 2:
                            AG[2,ii,jj]=F2[ii,jj]
                        if i == 3:
                            AG[3,ii,jj]=F3[ii,jj]
                        if i == 4:
                            AG[4,ii,jj]=F4[ii,jj]
                        if i == 5:
                            AG[5,ii,jj]=F5[ii,jj]
                        if i == 6:
                            AG[6,ii,jj]=F6[ii,jj]
                        if i == 7:
                            AG[7,ii,jj]=F7[ii,jj]

            for ii in range(M):
                for jj in range(M):
                    LI2[ii,jj]=0

            for i in range(M1):
                for ii in range(M):
                    for jj in range(M):
                        LI2[ii,jj]=LI2[ii,jj]+(DET1[i]*(10**DET2[i])*AG[i,ii,jj])/(DET10*(10**DET20))
            
            if n == 2:
                continue
            else:
                for ii in range(M):
                    for jj in range(M):
                        LI3[ii,jj]=LI2[ii,jj]


        F2 = DMCRCR(LI3,LI2)
        
######################## !!!!!!! PROBLEMS START HERE WITH GG, GG1 and GG2 !!!!!!!!! #################
        
        for i in range(M20):
            for j in range(M20):
                GG[i,j]=0.
                GG1[i,j]=0.
                GG2[i,j]=0.

        for i in range(M):
            GG[i,i]=1.
            GG[i,i+M]=1.
            GG[i+M,i+2*M]=1.
            GG[i+M,i+3*M]=1.
            GG1[i,i]=1.
            GG1[i,i+M]=1.
            GG1[i+M,i+2*M]=1.
            GG1[i+M,i+3*M]=1.
        
        for i in range(M):
            for j in range(M):
                GG[i+2*M,j]=-LU[i,j]
                GG[i+2*M,j+M]=LU[i,j]
                GG[i+3*M,j+2*M]=-1*LI[i,j]
                GG[i+3*M,j+3*M]=+LI[i,j]

                GG1[i+2*M,j]=LU3[i,j]
                GG1[i+2*M,j+M]=LU2[i,j]
                GG1[i+3*M,j+2*M]=LI3[i,j]
                GG1[i+3*M,j+3*M]=LI2[i,j]

        GG2 = DLINCG(M20,GG1) # Look for M20

        
#         print("GG :", GG)
#         print("GG1 :", GG1)
#         print("GG2 :", GG2)

    
        for i in range(M):
            for j in range(M):
                HH11[i,j]=GG2[i,j]
                HH12[i,j]=GG2[i,j+M]
                HH13[i,j]=GG2[i,j+2*M]
                HH14[i,j]=GG2[i,j+3*M]
                HH21[i,j]=GG2[i+M,j]
                HH22[i,j]=GG2[i+M,j+M]
                HH23[i,j]=GG2[i+M,j+2*M]
                HH24[i,j]=GG2[i+M,j+3*M]
                HH31[i,j]=GG2[i+2*M,j]
                HH32[i,j]=GG2[i+2*M,j+M]
                HH33[i,j]=GG2[i+2*M,j+2*M]
                HH34[i,j]=GG2[i+2*M,j+3*M]
                HH41[i,j]=GG2[i+3*M,j]
                HH42[i,j]=GG2[i+3*M,j+M]
                HH43[i,j]=GG2[i+3*M,j+2*M]
                HH44[i,j]=GG2[i+3*M,j+3*M]
        
        
#         print("HH11 :", HH11);
#         print("HH12 :", HH12);
#         print("HH13 :", HH13);
#         print("HH14 :", HH14);
#         print("HH21 :", HH21);
#         print("HH22 :", HH22);
#         print("HH23 :", HH23);
#         print("HH24 :", HH24);
#         print("HH31 :", HH31);
#         print("HH32 :", HH32);
#         print("HH33 :", HH33);
#         print("HH34 :", HH34);
#         print("HH41 :", HH41);
#         print("HH42 :", HH42);
#         print("HH43 :", HH43);
#         print("HH44 :", HH44);

        
        
        F = DMCRCR(LU3,HH11)
        HH11 = DMCRCR(LU,F)
        F = DMCRCR(LU2,HH21)
        HH21 = DMCRCR(LU,F)
        F = DMCRCR(LU3,HH13)
        HH13 = DMCRCR(LU,F)
        F = DMCRCR(LU2,HH23)
        HH23 = DMCRCR(LU,F)
        F = DMCRCR(LI3,HH32)
        HH32 = DMCRCR(LI,F)
        F = DMCRCR(LI2,HH42)
        HH42 = DMCRCR(LI,F)
        F = DMCRCR(LI3,HH34)
        HH34 = DMCRCR(LI,F)
        F = DMCRCR(LI2,HH44)
        HH44 = DMCRCR(LI,F)
        
#         print("HH11: ", HH11)
#         print("HH21: ", HH21)
#         print("HH13: ", HH13)
#         print("HH23: ", HH23)
#         print("HH32: ", HH32)
#         print("HH42: ", HH42)
#         print("HH34: ", HH34)
#         print("HH44: ", HH44)
#         print("F: ", F)
        
#         for i in range(M10):
#             for j in range(M20):
#                 GG3[i,j]=0.0

        for i in range(M):
            for j in range(M):
                GG3[i,j]=-1*HH11[i,j]+HH21[i,j]
                GG3[i,j+2*M]=-1*HH13[i,j]+HH23[i,j]
                GG3[i,j+3*M]=-1*Z[i,j]
                GG3[i+M,j+M]=-1*HH32[i,j]+HH42[i,j]
                GG3[i+M,j+2*M]=-1*Y[i,j]
                GG3[i+M,j+3*M]=-1*HH34[i,j]+HH44[i,j]
        
        K1=0
        K0=0

        for j in range(M20):

            if IH[j] == 1:
                K1=K1+1
            if IH[j] == 0:
                if IH[j] == 0:
                    K0=K0+1
                if IH[j] == 1:
                    continue
                   
                for i in range(M10):
                    GG5[i,K0-1]=GG3[i,j]

            else:
                for i in range(M10):
                    GG4[i,K1-1]=-1*GG3[i,j] # Original was -GG3[i,j]
                    B10[K1-1]=B5[j]

                    
        #  !!!!!!!!!!!!!!!!!!!!        B10          !!!!!!!!!!!!!!!!!!!!!!!!


#         print("B10: ", B10)
#         print("GG4: ", GG4)
        B6 = DMUCRV(GG4,B10)     
#         print("B6: ", B6)
#         print("GG5: ", GG5)
        B7 = DLSLCG(GG5,B6)
        
#         print("B7: ", B7)  # B7 is the REAL PROBLEM. HAS TO BE CORRECTED   !!!!!!!!!!!!!!!!!!
        
#         print("GG5: ", GG5)
#         print("GG4: ", GG4)
#         print("B10: ", B10)
#         print("B6: ", B6)
#         print("B7: ", B7)
        
        K1=0

        for j in range(M20):
            if IH[j] == 0:
                K1=K1+1
            if IH[j] == 1:
                continue

            B5[j]=B7[K1-1]
#         print("B5: ", B5)  # B5 is the REAL PROBLEM. HAS TO BE CORRECTED   !!!!!!!!!!!!!!!!!!
        for i in range(M):
            UK1[i]=B5[i]
            AIK1[i]=B5[i+M]
        
#         print("Z: ", Z)
#         print("Y: ", Y)
#         print("AIK1: ", AIK1)   # AIK1 SHOLD BE CORRECTED !!!!!!!!!!!!!!!!!!!!!!!!!!
#         print("UK1: ", UK1)     # UK1 SHOLD BE CORRECTED !!!!!!!!!!!!!!!!!!!!!!!!!!
        
        AA = DMUCRV(Z,AIK1)
        BB = DMUCRV(Y,UK1)
        CC = DMCRCR(LI,LI3)
        DD = DMCRCR(LI,LI2)
        
#         print("AA:", AA)
#         print("BB:", BB)
#         print("CC:", CC)
#         print("DD:", DD)
        
        for i in range(M):
            B1[i]=UK1[i]
            B1[i+M]=AIK1[i]
            B1[i+2*M]=AA[i]
            B1[i+3*M]=BB[i]
        
        B4 = DLSLCG(GG,B1)
        
        for i in range(M):
            AA[i]=0.
            B[i]=0.
            B[i]=B4[i]

        AA = DMUCRV(LU3,B)

        for i in range(M):
            BB[i]=0.
            B[i]=0.
            B[i]=B4[i+M]

        BB = DMUCRV(LU2,B)

        for i in range(M):
            UX[i]=AA[i]+BB[i]
            if LM == MMT:
                UK1[i]=UX[i]
            UXM[i]=np.sqrt(UX[i].real**2+UX[i].imag**2)

        for i in range(M):
            AA[i]=0.
            B[i]=0.
            B[i]=B4[i+2*M]
        
        AA = DMUCRV(LI3,B)   # NEED TO CORRECT AA !!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!
        
        for i in range(M):
            BB[i]=0.
            B[i]=0.
            B[i]=B4[i+3*M]
        
        BB = DMUCRV(LI2,B)   # NEED TO CORRECT BB !!!!!!!!!!!!!!!!!!!!!!!!!!!!!!!
        
        for i in range(M):
                    
            AIX[i]=AA[i]+BB[i]
            if LM == MMT:
                AIK1[i]=AIX[i]
            AIXM[i]=np.sqrt(AIX[i].real**2+AIX[i].imag**2)
            
########################### PROBLEM LIES IN    !!!!  AIX  !!!!  ###################################### 

#             print("AIX: ", AIX)
#             print("AIXM: ", AIXM)
#             print("R11: ", R11)
            
            if i == 0 and LL == 0 and PR == 2:
                PPP1[NN,LL]=PPP1[NN,LL]+AIXM[0]**2/2*R11[0]
            if i == 0 and LL > 0:
                PPP1[NN,LL]=PPP1[NN,LL]+AIXM[0]**2/2*R11[0]
            if i == 1 and LL == 0 and PR == 2:
                PPP2[NN,LL]=PPP2[NN,LL]+AIXM[1]**2/2*R11[1]
            if i == 1 and LL > 0:
                PPP2[NN,LL]=PPP2[NN,LL]+AIXM[1]**2/2*R11[1]
            if i == 2 and LL == 0 and PR == 2:
                PPP3[NN,LL]=PPP3[NN,LL]+AIXM[2]**2/2*R11[2]
            if i == 2 and LL > 0:
                PPP3[NN,LL]=PPP3[NN,LL]+AIXM[2]**2/2*R11[2]
            if i == 3 and LL == 0 and PR == 2:
                PPP4[NN,LL]=PPP4[NN,LL]+AIXM[3]**2/2*R11[3]
            if i == 3 and LL > 0:
                PPP4[NN,LL]=PPP4[NN,LL]+AIXM[3]**2/2*R11[3]
            if i == 4 and LL == 0 and PR == 2:
                PPP5[NN,LL]=PPP5[NN,LL]+AIXM[4]**2/2*R11[4]
            if i == 4 and LL > 0:
                PPP5[NN,LL]=PPP5[NN,LL]+AIXM[4]**2/2*R11[4]
            if i == 5 and LL == 0 and PR == 2:
                PPP6[NN,LL]=PPP6[NN,LL]+AIXM[5]**2/2*R11[5]
            if i == 5 and LL > 0:
                PPP6[NN,LL]=PPP6[NN,LL]+AIXM[5]**2/2*R11[5]
            if i == 6 and LL == 0 and PR == 2:
                PPP7[NN,LL]=PPP7[NN,LL]+AIXM[6]**2/2*R11[6]
            if i == 6 and LL > 0:
                PPP7[NN,LL]=PPP7[NN,LL]+AIXM[6]**2/2*R11[6]
            if i == 7 and LL == 0 and PR == 2:
                PPP8[NN,LL]=PPP8[NN,LL]+AIXM[7]**2/2*R11[7]
            if i == 7 and LL > 0:
                PPP8[NN,LL]=PPP8[NN,LL]+AIXM[7]**2/2*R11[7]
            if LL == 0 and PR == 2.:
                PPP[NN,LL]=PPP[NN,LL]+AIXM[i]**2/2*R11[i]
            if LL > 0:
                PPP[NN,LL]=PPP[NN,LL]+AIXM[i]**2/2*R11[i]
            if LL == 0 and PR == 1.:
                PP1=PP1+AIXM[i]**2/2*R11[i]
            if LL == 0 and PR == 2.:
                PP2=PP2+AIX[i]**2/2*R11[i]
            SM[i]=UX[i]*np.conj(AIX[i])/2.
            
#             print(PPP1[NN, LL])

        # Writing UXM and AIXM values into 10th and 11th modules    

In [131]:
# !!!  470th loop stands for 1th or one prisoed of podstanst  !!!

# 11 - 13
for i in range(560+1):
    for p in range(3):
        UM[i,0,p] = funu[i,p]*np.sqrt(2) 
        FUM[i,0,p]=fu[i,p]*np.pi/180 
        UM1[i,0,p]=UM[i,0,p]*np.cos(FUM[i,0,p]) 
        UM2[i,0,p]=UM[i,0,p]*np.sin(FUM[i,0,p])     
        
# 13 - 14
for i in range(560+1):
    for p in range(3):
        for k in range(50-1):
            UM[i,k+1,p]=UM[i,k+1,p]*UM[i,0,p]/100.
            FUM[i,k+1,p]=FUM[i,k+1,p]*np.pi/180.
            UM1[i,k+1,p]=UM[i,k+1,p]*np.cos(FUM[i,k+1,p])
            UM2[i,k+1,p]=UM[i,k+1,p]*np.sin(FUM[i,k+1,p])

# 14 - 16
for i in range(560+1):
    for p in range(3):
        AIM[i,0,p]=funi[i,p]*np.sqrt(2)
        FIM[i,0,p]=fi[i,p]*np.pi/180
        AIM1[i,0,p]=AIM[i,0,p]*np.cos(FIM[i,0,p])
        AIM2[i,0,p]=AIM[i,0,p]*np.sin(FIM[i,0,p])
        
# 16 - 117
for i in range(560+1):
    for p in range(3):
        for k in range(50-1):
            AIM[i,k+1,p]=AIM[i,k+1,p]*AIM[i,0,p]/100
            FIM[i,k+1,p]=FIM[i,k+1,p]*np.pi/180
            AIM1[i,k+1,p]=AIM[i,k+1,p]*np.cos(FIM[i,k+1,p])
            AIM2[i,k+1,p]=AIM[i,k+1,p]*np.sin(FIM[i,k+1,p])
        

In [132]:
#  !!!!!!!!!!!!!!!!!!!!!!!!!! WATCH OUT WITH UK1 and AIK1 !!!!!!!!!!!!!!!!!!!!!

In [133]:
# 117 - 1700 - 1500

print("!!! Started !!!")

MM, MPR, MTR, DT, MT = 5, 3, 1, 2.5, 5 #         <---- INPUT FROM THE USER
M = MPR + MTR     # thus is 4
MMT = MM / MT    # is 1

if M <= 6:
    M1 = M
if M > 6:
    M1 = 6

M10 = 2 * M # is 8
M20 = 4 * M # is 16

n = LoopI(0, 50) # OUTER LOOP
k = LoopI(0, 560) # INNTER LOOP
PR = LoopI(0, 5000000)
counter = 1

start = time.time()

while True:


    if k.the_end:
        break
    K = k.get_current_index(); N = n.get_current_index();
    if N > 49:
        N = 49
    UK1[0] = complex(UM1[K,N,0], UM2[K,N,0])
    UK1[1] = complex(UM1[K,N,1], UM2[K,N,1])
    UK1[2] = complex(UM1[K,N,2], UM2[K,N,2])
    UK1[3] = complex(0, 0)
    AIK1[0] = complex(AIM1[K,N,0], AIM2[K,N,0])
    AIK1[1] = complex(AIM1[K,N,1], AIM2[K,N,1])
    AIK1[2] = complex(AIM1[K,N,2], AIM2[K,N,2])
    AIK1[3] = complex(0, 0)

    if not (n.get_current_index() > 0) or (k.get_current_index() == 0 and PR.get_current_index() ==2):
        
        UK10=(UK1[0]+UK1[1]+UK1[2])/3
        UK11=(UK1[0]+UK1[1]*AL+UK1[2]*AL**2)/3
        UK12=(UK1[0]+UK1[1]*AL**2+UK1[2]*AL)/3
        SKU2=np.sqrt(UK12.real**2+UK12.imag**2)/np.sqrt(UK11.real**2+UK11.imag**2)*100
        SKU0=np.sqrt(UK10.real**2+UK10.imag**2)/np.sqrt(UK11.real**2+UK11.imag**2)*100
        UK1[0]=UK11
        UK1[1]=UK11*AL**2
        UK1[2]=UK11*AL
        AIK10=(AIK1[0]+AIK1[1]+AIK1[2])/3
        AIK11=(AIK1[0]+AIK1[1]*AL+AIK1[2]*AL**2)/3
        AIK12=(AIK1[0]+AIK1[1]*AL**2+AIK1[2]*AL)/3
        SKI2=np.sqrt(AIK12.real**2+AIK12.imag**2)/np.sqrt(AIK11.real**2+AIK11.imag**2)*100
        SKI0=np.sqrt(AIK10.real**2+AIK10.imag**2)/np.sqrt(AIK11.real**2+AIK11.imag**2)*100
        AIK1[1]=AIK11
        AIK1[2]=AIK11*AL**2
        AIK1[3]=AIK11*AL


    RASCHET(K, N)


    if k.get_current_index() == 0 and PR.get_current_index() == 1:
        pass
    if k.get_current_index() == 0 and PR.get_current_index() == 2:
        pass
    if k.get_current_index() == 0 and PR.get_current_index() == 1:
        PR.step_up_index()
        continue
    if PR.get_current_index() == 2:
        PR.set_current_index(0)

    if n.the_end:
        k.step_up_index()
        n.set_current_index(0)
    else:
        n.step_up_index()

print("!!! Finished !!!")
end = time.time()
print("Time took(sec): ", end - start)

!!! Started !!!
1.0
CHECK : [[0.74827675 0.31909562 0.30961206 0.29496562]
 [0.31909562 0.74827675 0.31852956 0.29043115]
 [0.30961206 0.31852956 0.74827675 0.35326141]
 [0.29496562 0.29043115 0.35326141 0.78286804]]
2.0
CHECK : [[1.4965535  0.63819124 0.61922413 0.58993124]
 [0.63819124 1.4965535  0.63705912 0.58086231]
 [0.61922413 0.63705912 1.4965535  0.70652283]
 [0.58993124 0.58086231 0.70652283 1.56573608]]
3.0
CHECK : [[2.24483025 0.95728686 0.92883619 0.88489685]
 [0.95728686 2.24483025 0.95558868 0.87129346]
 [0.92883619 0.95558868 2.24483025 1.05978424]
 [0.88489685 0.87129346 1.05978424 2.34860412]]
4.0
CHECK : [[2.993107   1.27638248 1.23844826 1.17986247]
 [1.27638248 2.993107   1.27411823 1.16172461]
 [1.23844826 1.27411823 2.993107   1.41304565]
 [1.17986247 1.16172461 1.41304565 3.13147216]]
5.0
CHECK : [[3.74138375 1.5954781  1.54806032 1.47482809]
 [1.5954781  3.74138375 1.59264779 1.45215576]
 [1.54806032 1.59264779 3.74138375 1.76630707]
 [1.47482809 1.45215576 1.7

2.0
CHECK : [[1.4965535  0.63819124 0.61922413 0.58993124]
 [0.63819124 1.4965535  0.63705912 0.58086231]
 [0.61922413 0.63705912 1.4965535  0.70652283]
 [0.58993124 0.58086231 0.70652283 1.56573608]]
3.0
CHECK : [[2.24483025 0.95728686 0.92883619 0.88489685]
 [0.95728686 2.24483025 0.95558868 0.87129346]
 [0.92883619 0.95558868 2.24483025 1.05978424]
 [0.88489685 0.87129346 1.05978424 2.34860412]]
4.0
CHECK : [[2.993107   1.27638248 1.23844826 1.17986247]
 [1.27638248 2.993107   1.27411823 1.16172461]
 [1.23844826 1.27411823 2.993107   1.41304565]
 [1.17986247 1.16172461 1.41304565 3.13147216]]
5.0
CHECK : [[3.74138375 1.5954781  1.54806032 1.47482809]
 [1.5954781  3.74138375 1.59264779 1.45215576]
 [1.54806032 1.59264779 3.74138375 1.76630707]
 [1.47482809 1.45215576 1.76630707 3.9143402 ]]
6.0
CHECK : [[4.4896605  1.91457372 1.85767239 1.76979371]
 [1.91457372 4.4896605  1.91117735 1.74258692]
 [1.85767239 1.91117735 4.4896605  2.11956848]
 [1.76979371 1.74258692 2.11956848 4.697208

50.0
CHECK : [[37.41383747 15.95478102 15.48060321 14.74828088]
 [15.95478102 37.41383747 15.92647792 14.52155764]
 [15.48060321 15.92647792 37.41383747 17.66307068]
 [14.74828088 14.52155764 17.66307068 39.14340202]]
1.0
CHECK : [[0.74827675 0.31909562 0.30961206 0.29496562]
 [0.31909562 0.74827675 0.31852956 0.29043115]
 [0.30961206 0.31852956 0.74827675 0.35326141]
 [0.29496562 0.29043115 0.35326141 0.78286804]]
2.0
CHECK : [[1.4965535  0.63819124 0.61922413 0.58993124]
 [0.63819124 1.4965535  0.63705912 0.58086231]
 [0.61922413 0.63705912 1.4965535  0.70652283]
 [0.58993124 0.58086231 0.70652283 1.56573608]]
3.0
CHECK : [[2.24483025 0.95728686 0.92883619 0.88489685]
 [0.95728686 2.24483025 0.95558868 0.87129346]
 [0.92883619 0.95558868 2.24483025 1.05978424]
 [0.88489685 0.87129346 1.05978424 2.34860412]]
4.0
CHECK : [[2.993107   1.27638248 1.23844826 1.17986247]
 [1.27638248 2.993107   1.27411823 1.16172461]
 [1.23844826 1.27411823 2.993107   1.41304565]
 [1.17986247 1.16172461 1.

48.0
CHECK : [[35.91728398 15.31658978 14.86137908 14.15834965]
 [15.31658978 35.91728398 15.2894188  13.94069534]
 [14.86137908 15.2894188  35.91728398 16.95654785]
 [14.15834965 13.94069534 16.95654785 37.57766594]]
49.0
CHECK : [[36.66556072 15.6356854  15.17099115 14.45331527]
 [15.6356854  36.66556072 15.60794836 14.23112649]
 [15.17099115 15.60794836 36.66556072 17.30980927]
 [14.45331527 14.23112649 17.30980927 38.36053398]]
50.0
CHECK : [[37.41383747 15.95478102 15.48060321 14.74828088]
 [15.95478102 37.41383747 15.92647792 14.52155764]
 [15.48060321 15.92647792 37.41383747 17.66307068]
 [14.74828088 14.52155764 17.66307068 39.14340202]]
50.0
CHECK : [[37.41383747 15.95478102 15.48060321 14.74828088]
 [15.95478102 37.41383747 15.92647792 14.52155764]
 [15.48060321 15.92647792 37.41383747 17.66307068]
 [14.74828088 14.52155764 17.66307068 39.14340202]]
1.0
CHECK : [[0.74827675 0.31909562 0.30961206 0.29496562]
 [0.31909562 0.74827675 0.31852956 0.29043115]
 [0.30961206 0.3185295

44.0
CHECK : [[32.92417698 14.04020729 13.62293083 12.97848718]
 [14.04020729 32.92417698 14.01530057 12.77897073]
 [13.62293083 14.01530057 32.92417698 15.5435022 ]
 [12.97848718 12.77897073 15.5435022  34.44619378]]
45.0
CHECK : [[33.67245373 14.35930291 13.93254289 13.27345279]
 [14.35930291 33.67245373 14.33383013 13.06940188]
 [13.93254289 14.33383013 33.67245373 15.89676361]
 [13.27345279 13.06940188 15.89676361 35.22906182]]
46.0
CHECK : [[34.42073048 14.67839854 14.24215495 13.56841841]
 [14.67839854 34.42073048 14.65235968 13.35983303]
 [14.24215495 14.65235968 34.42073048 16.25002503]
 [13.56841841 13.35983303 16.25002503 36.01192986]]
47.0
CHECK : [[35.16900723 14.99749416 14.55176702 13.86338403]
 [14.99749416 35.16900723 14.97088924 13.65026419]
 [14.55176702 14.97088924 35.16900723 16.60328644]
 [13.86338403 13.65026419 16.60328644 36.7947979 ]]
48.0
CHECK : [[35.91728398 15.31658978 14.86137908 14.15834965]
 [15.31658978 35.91728398 15.2894188  13.94069534]
 [14.86137908

...

26.0
CHECK : [[19.45519549  8.29648613  8.04991367  7.66910606]
 [ 8.29648613 19.45519549  8.28176852  7.55120998]
 [ 8.04991367  8.28176852 19.45519549  9.18479675]
 [ 7.66910606  7.55120998  9.18479675 20.35456905]]
27.0
CHECK : [[20.20347224  8.61558175  8.35952573  7.96407168]
 [ 8.61558175 20.20347224  8.60029808  7.84164113]
 [ 8.35952573  8.60029808 20.20347224  9.53805817]
 [ 7.96407168  7.84164113  9.53805817 21.13743709]]
28.0
CHECK : [[20.95174899  8.93467737  8.6691378   8.25903729]
 [ 8.93467737 20.95174899  8.91882763  8.13207228]
 [ 8.6691378   8.91882763 20.95174899  9.89131958]
 [ 8.25903729  8.13207228  9.89131958 21.92030513]]
29.0
CHECK : [[21.70002574  9.25377299  8.97874986  8.55400291]
 [ 9.25377299 21.70002574  9.23735719  8.42250343]
 [ 8.97874986  9.23735719 21.70002574 10.24458099]
 [ 8.55400291  8.42250343 10.24458099 22.70317317]]
30.0
CHECK : [[22.44830248  9.57286861  9.28836193  8.84896853]
 [ 9.57286861 22.44830248  9.55588675  8.71293459]
 [ 9.28836193

23.0
CHECK : [[17.21036524  7.33919927  7.12107748  6.78420921]
 [ 7.33919927 17.21036524  7.32617984  6.67991652]
 [ 7.12107748  7.32617984 17.21036524  8.12501251]
 [ 6.78420921  6.67991652  8.12501251 18.00596493]]
24.0
CHECK : [[17.95864199  7.65829489  7.43068954  7.07917482]
 [ 7.65829489 17.95864199  7.6447094   6.97034767]
 [ 7.43068954  7.6447094  17.95864199  8.47827393]
 [ 7.07917482  6.97034767  8.47827393 18.78883297]]
25.0
CHECK : [[18.70691874  7.97739051  7.74030161  7.37414044]
 [ 7.97739051 18.70691874  7.96323896  7.26077882]
 [ 7.74030161  7.96323896 18.70691874  8.83153534]
 [ 7.37414044  7.26077882  8.83153534 19.57170101]]
26.0
CHECK : [[19.45519549  8.29648613  8.04991367  7.66910606]
 [ 8.29648613 19.45519549  8.28176852  7.55120998]
 [ 8.04991367  8.28176852 19.45519549  9.18479675]
 [ 7.66910606  7.55120998  9.18479675 20.35456905]]
27.0
CHECK : [[20.20347224  8.61558175  8.35952573  7.96407168]
 [ 8.61558175 20.20347224  8.60029808  7.84164113]
 [ 8.35952573

21.0
CHECK : [[15.71381174  6.70100803  6.50185335  6.19427797]
 [ 6.70100803 15.71381174  6.68912073  6.09905421]
 [ 6.50185335  6.68912073 15.71381174  7.41848969]
 [ 6.19427797  6.09905421  7.41848969 16.44022885]]
22.0
CHECK : [[16.46208849  7.02010365  6.81146541  6.48924359]
 [ 7.02010365 16.46208849  7.00765028  6.38948536]
 [ 6.81146541  7.00765028 16.46208849  7.7717511 ]
 [ 6.48924359  6.38948536  7.7717511  17.22309689]]
23.0
CHECK : [[17.21036524  7.33919927  7.12107748  6.78420921]
 [ 7.33919927 17.21036524  7.32617984  6.67991652]
 [ 7.12107748  7.32617984 17.21036524  8.12501251]
 [ 6.78420921  6.67991652  8.12501251 18.00596493]]
24.0
CHECK : [[17.95864199  7.65829489  7.43068954  7.07917482]
 [ 7.65829489 17.95864199  7.6447094   6.97034767]
 [ 7.43068954  7.6447094  17.95864199  8.47827393]
 [ 7.07917482  6.97034767  8.47827393 18.78883297]]
25.0
CHECK : [[18.70691874  7.97739051  7.74030161  7.37414044]
 [ 7.97739051 18.70691874  7.96323896  7.26077882]
 [ 7.74030161

21.0
CHECK : [[15.71381174  6.70100803  6.50185335  6.19427797]
 [ 6.70100803 15.71381174  6.68912073  6.09905421]
 [ 6.50185335  6.68912073 15.71381174  7.41848969]
 [ 6.19427797  6.09905421  7.41848969 16.44022885]]
22.0
CHECK : [[16.46208849  7.02010365  6.81146541  6.48924359]
 [ 7.02010365 16.46208849  7.00765028  6.38948536]
 [ 6.81146541  7.00765028 16.46208849  7.7717511 ]
 [ 6.48924359  6.38948536  7.7717511  17.22309689]]
23.0
CHECK : [[17.21036524  7.33919927  7.12107748  6.78420921]
 [ 7.33919927 17.21036524  7.32617984  6.67991652]
 [ 7.12107748  7.32617984 17.21036524  8.12501251]
 [ 6.78420921  6.67991652  8.12501251 18.00596493]]
24.0
CHECK : [[17.95864199  7.65829489  7.43068954  7.07917482]
 [ 7.65829489 17.95864199  7.6447094   6.97034767]
 [ 7.43068954  7.6447094  17.95864199  8.47827393]
 [ 7.07917482  6.97034767  8.47827393 18.78883297]]
25.0
CHECK : [[18.70691874  7.97739051  7.74030161  7.37414044]
 [ 7.97739051 18.70691874  7.96323896  7.26077882]
 [ 7.74030161

23.0
CHECK : [[17.21036524  7.33919927  7.12107748  6.78420921]
 [ 7.33919927 17.21036524  7.32617984  6.67991652]
 [ 7.12107748  7.32617984 17.21036524  8.12501251]
 [ 6.78420921  6.67991652  8.12501251 18.00596493]]
24.0
CHECK : [[17.95864199  7.65829489  7.43068954  7.07917482]
 [ 7.65829489 17.95864199  7.6447094   6.97034767]
 [ 7.43068954  7.6447094  17.95864199  8.47827393]
 [ 7.07917482  6.97034767  8.47827393 18.78883297]]
25.0
CHECK : [[18.70691874  7.97739051  7.74030161  7.37414044]
 [ 7.97739051 18.70691874  7.96323896  7.26077882]
 [ 7.74030161  7.96323896 18.70691874  8.83153534]
 [ 7.37414044  7.26077882  8.83153534 19.57170101]]
26.0
CHECK : [[19.45519549  8.29648613  8.04991367  7.66910606]
 [ 8.29648613 19.45519549  8.28176852  7.55120998]
 [ 8.04991367  8.28176852 19.45519549  9.18479675]
 [ 7.66910606  7.55120998  9.18479675 20.35456905]]
27.0
CHECK : [[20.20347224  8.61558175  8.35952573  7.96407168]
 [ 8.61558175 20.20347224  8.60029808  7.84164113]
 [ 8.35952573

In [ ]:
# 1500 - 1501

for n in range(560):
    PRP = 0
    for k in range(50): # 1060'th loop
        PRP=PRP+PPP[n,k]
    RPR=0
    for k in range(50-1): # 1061'st loop
        RPR=RPR+PPP[n,k+1]
    
    SS1=(PPP[n,0]/PPR1[n]-1)*100
    SS2=(RPR/PPR1[n])*100
    SS0=PPP[n,0]-PPR1[n]
    
    # WRITING INTO "PPP" and "PPPx" files corresponding PPP and PPPx values
#     print(PPP1[n, k])
    
# 1501 - 1052
WD0=0.
for k in range(50):
    WD[0,k]=0
    for i in range(560):
        WD0=WD0+PPP[i,k]*DT/60000
        WD[0,k]=WD[0,k]+PPP[i,k]*DT/60000

# 1052 - 1057
WD1=WD0-WD[0,0]
for k in range(50):
    WD[1,k]=WD[0,k]/WD0*100
WD4=0
for k in range(13, 50):
    WD4=WD4+WD[1,k]
WD10=0
for i in range(560):
    WD10=WD10+PPR1[i]*DT/60000
 
# 1057 -1054
for i in range(560):
    PD[0,i] = 0
    PD[1,i] = 0
    for k in range(50):
        PD[0,i]=PD[0,i]+PPP[i,k]
    PD[1,i]=PD[0,i]-PPP[i,0]
    PD[2,i]=PD[1,i]/PD[0,i]*100

# WRITING CALCULATION RESULTS INTO 8th UNIT (Результаты расчета)